<a href="https://colab.research.google.com/github/pansplawik/eegParkinsonCognitiveDisorders/blob/master/secondVersion.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install mne

Importowanie pakietów

In [2]:
import mne
import numpy as np
import matplotlib.pyplot as plt
import os
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
import csv
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
from mne.decoding import PSDEstimator

Ściezki plików

In [14]:
labels = pd.read_csv("C:/Users/splaw/OneDrive/Pulpit/dyplom/eegParkinsonCognitiveDisorders/dataset.csv", sep=';')
path='C:/Users/splaw/OneDrive/Pulpit/dyplom/EEG'

Preprocesing danych

In [8]:
def load_epochs_from_dir(path, labels):
    epochs_array = []
    for filename, label in zip(os.listdir(path), labels['PD']):
        print(filename)
        if filename.endswith('.edf'):
            filepath = os.path.join(path, filename)
            raw = mne.io.read_raw_edf(filepath, preload=True)
            annotations = raw.annotations
            change=0
            for i in range(len(annotations)):
              if annotations.description[i] == "break":
                annotations.description[i] = "BAD" 
                change=change+1
              elif annotations.description[i] == 'Break end':
                annotations.description[i] = "BAD"
                change=change+1
              elif annotations.description[i] == 'Miesnie':
                annotations.description[i] = "BAD"
                change=change+1
              elif annotations.description[i] == 'Break start':
                annotations.description[i] = "BAD"
                change=change+1
              elif annotations.description[i] == 'Ruch':
                annotations.description[i] = "BAD"
                change=change+1
            print(change)
            raw.set_annotations(annotations)
            raw.filter(1, 40, fir_design='firwin')
            events = mne.make_fixed_length_events(raw, duration=1.0)
            reject = dict(     
              eeg=80e-6,       
              )
            epochs = mne.Epochs(raw, events, tmin=0, tmax=2, baseline=(0,2), detrend=1,reject_by_annotation='BAD',preload=True,reject=reject)
            epochs_array.append([epochs,label])
            print()
            print(epochs.drop_log)
            del epochs
            del raw
            del annotations
    return epochs_array


PSD

In [11]:
def psds(epochs_array, labels):
    data = []
    for epochs, label in zip(epochs_array, labels):
      if epochs is not None and len(epochs) > 0:
        epo_spectrum = mne.time_frequency.psd_array_multitaper(x=epochs_data, sfreq=512, fmin=1, fmax=40, verbose=False)
        psds, freqs = epo_spectrum
        vector=[]
        for p in psds:
            p = 10 * np.log10(p)
            vector.append(p)
            data.append(np.mean(vector))
        del psds
        del freqs
    return data

In [15]:
data = load_epochs_from_dir(path,labels)
df = pd.DataFrame(data, columns=['value', 'label'])
df.to_csv('data.csv', index=False)

PD129.edf
Extracting EDF parameters from C:\Users\splaw\OneDrive\Pulpit\dyplom\EEG\PD129.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 755199  =      0.000 ...  1474.998 secs...
41
Filtering raw data in 1 contiguous segment
Setting up band-pass filter from 1 - 40 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Upper passband edge: 40.00 Hz
- Upper transition bandwidth: 10.00 Hz (-6 dB cutoff frequency: 45.00 Hz)
- Filter length: 1691 samples (3.303 s)



[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.2s remaining:    0.0s


Not setting metadata
1475 matching events found
Applying baseline correction (mode: mean)
0 projection items activated
Using data from preloaded Raw for 1475 events and 1025 original time points ...


[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    1.7s finished


    Rejecting  epoch based on EEG : ['Oz']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
   

...

    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P4', 'T5', 'T6']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz']
    Rejecting  epoch based on EEG : ['F8', 'Oz', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F4', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F4', 'F7', 'F8', 'Fp2

    Rejecting  epoch based on EEG : ['C4', 'Cz', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T4']
    Rejecting  epoch based on EEG : ['C4', 'F8', 'O1', 'O2', 'Oz', 'P4', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['F8', 'O1', 'O2', 'Oz', 'T5', 'T6']
    Rejecting  epoch based on EEG : ['F8', 'O1', 'Oz']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P3', 'P4', 'Pz']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P3', 'P4', 'Pz']
    Rejecting  epoch based on EEG : ['O2', 'Oz', 'P4']
    Rejecting  epoch based on EEG : ['Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['Cz', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C4', 'Cz', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6

    Rejecting  epoch based on EEG : ['C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['Oz']
    Rejecting  epoch based on EEG : ['Oz']
    Rejecting  epoch based on EEG : ['Oz']
    Rejecting  epoch based on EEG : ['Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['F7', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C4', 'F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F7', 'F8', 'O1', 'O2', 'Oz

    Rejecting  epoch based on EEG : ['C3', 'Cz', 'F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P3', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['F7', 'Oz', 'P4', 'T5', 'T6']
    Rejecting  epoch based on EEG : ['F7', 'Oz', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['T6']
    Rejecting  epoch based on EEG : ['T6', 'T4']
    Rejecting  epoch based on EEG : ['F8', 'O1', 'O2', 'Oz', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['F7', 'O1', 'O2', 'Oz', 'P4', 'T5', 'T6', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['F7', 'O2', 'Oz', 'T5', 'T3']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P4', 'T5', 'T6', 'T4']
    Rejecting  epoch based on EEG : ['O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['F8', 'O1', 'O2', 'Oz', 'P3', 'P4

    Rejecting  epoch based on EEG : ['F7', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
    Rejecting  epoch based on EEG : ['C3', 'C4', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4']
1225 bad epochs dropped

(('C4', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4'), ('C3', 'C4', 'Cz', 'F7', 'F8', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4'), ('C3', 'C4', 'Cz', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4'), ('C4', 'F7', 'F8', 'O1', 'O2', 'Oz', 'P4', 'T5', 'T6', 'T3', 'T4'), ('F7', 'F8', 'O1', 'O2', 'Oz', 'P4', 'T5', 'T6', 'T3', 'T4'), ('BAD',), ('BAD',), ('BAD',), ('BAD',), ('BAD',), ('BAD',), ('O2', 'Oz'), ('O2', 'Oz'), ('C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4'), ('C3', 'C4', 'Cz', 'F3', 'F4', 'F7', 'F8', 'Fz', 'Fp1', 'Fp2', 'O1', 'O2', 'Oz', 'P3', 'P4', 'T5', 'T6', 'Pz', 'T3', 'T4'), ('C3',

In [16]:
psd = psds([epochs for epochs, label in data], [label for epochs, label in data])
df = pd.DataFrame(psd, columns=['psds', 'label'])
df.to_csv('psd.csv', index=False)

NameError: name 'epochs_data' is not defined

Tworzenie zestawów

In [8]:
X_train, X_test, y_train, y_test = train_test_split([x[0] for x in psd], [x[1] for x in psd], test_size=0.2, random_state=42)
X_train_2d = np.array([x[0] for x in X_train]).reshape(len(X_train), -1)
X_test_2d = np.array([x[0] for x in X_test]).reshape(len(X_test), -1)
y_train=np.array(y_train)
y_train=y_train.transpose()
y_test=np.array(y_test)
y_test=y_test.transpose()

Tworzenie modelu

In [9]:
from mne.decoding import Vectorizer
from sklearn.svm import SVC
from sklearn.metrics import classification_report,confusion_matrix
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import precision_recall_fscore_support, accuracy_score
from sklearn.model_selection import cross_val_score, StratifiedGroupKFold
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix, accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import StratifiedKFold, cross_validate
k_folds = 5
skf = StratifiedGroupKFold(n_splits=k_folds, shuffle=True, random_state=42)
# Resetyowanie list, ponieważ wcześniejszy kod je zmienił
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []
# Przykładowe dane (zamień je na swoje dane)
X = df['psds'].values
y = df['label'].values
groups = df['pat_id'].values
# Wykonaj walidację krzyżową Stratified K-Fold
for fold, (train_index, test_index) in enumerate(skf.split(X, y, groups)):
    print(1)
    X_train, X_test = X[train_index], X[test_index]
    y_train, y_test = y[train_index], y[test_index]
    clf_svm_pip = make_pipeline(Vectorizer(), StandardScaler(), SVC())
    clf_svm_pip.fit(list(X_train), y_train)
    predictions_svm = clf_svm_pip.predict(list(X_test))
    accuracy_scores.append(accuracy_score(y_test, predictions_svm))
    precision_scores.append(precision_score(y_test, predictions_svm))
    recall_scores.append(recall_score(y_test, predictions_svm))
    f1_scores.append(f1_score(y_test, predictions_svm))

# Oblicz średnie statystyki ze wszystkich foldów
mean_accuracy = np.mean(accuracy_scores)
mean_precision = np.mean(precision_scores)
mean_recall = np.mean(recall_scores)
mean_f1 = np.mean(f1_scores)

# Wyświetl średnie statystyki
print("Mean Accuracy:", mean_accuracy)
print("Mean Precision:", mean_precision)
print("Mean Recall:", mean_recall)
print("Mean F1 Score:", mean_f1)

# Wykresy słupkowe dla wyników każdego foldu
fig, ax = plt.subplots(figsize=(8, 6))
x_labels = [f"Fold {fold+1}" for fold in range(k_folds)]
x = np.arange(len(x_labels))
width = 0.2

ax.bar(x - 1.5 * width, accuracy_scores, width, label='Accuracy')
ax.bar(x - 0.5 * width, precision_scores, width, label='Precision')
ax.bar(x + 0.5 * width, recall_scores, width, label='Recall')
ax.bar(x + 1.5 * width, f1_scores, width, label='F1 Score')

ax.set_xticks(x)
ax.set_xticklabels(x_labels)
ax.set_xlabel('Fold')
ax.set_ylabel('Scores')
ax.set_title('Scores for each Fold')
ax.legend()
plt.tight_layout()
plt.show()


(13047, 78)
(52187, 78)


SVC(C=1, kernel='linear', random_state=42)

Trening i wizualizacja wyników

In [10]:
y_pred = svm.predict(X_test_2d)
from sklearn.metrics import accuracy_score
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.45136813060473674


In [11]:
from joblib import dump, load
dump(svm, 'piaty.joblib') 

['piaty.joblib']